In [1]:
import ast
import csv
import json
import reverse_geocoder as rg

import numpy as np
import pandas as pd

import pycountry_convert

import matplotlib.pyplot as plt
from matplotlib_venn import venn2, venn2_circles

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

## Loading datasets

**re3data**

In [3]:
re3data_df = pd.read_csv('../data/raw/re3data.tsv', delimiter='\t', 
                        converters={'subject': ast.literal_eval,
                                    'keyword': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'repository_id': ast.literal_eval,
                                    'type': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'provider_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    },
                        usecols=['re3data_id', 'repository_name', 'subject', 'keyword', 'type', 'provider_type', 'institution'])
re3data_df.head()

re3data_id                   repository_name             type  \
0  r3d100000001  Odum Institute Archive Dataverse   [disciplinary]   
1  r3d100000002      Access to Archival Databases   [disciplinary]   
2  r3d100000004    Datenbank Gesprochenes Deutsch   [disciplinary]   
3  r3d100000005                     UNC Dataverse  [institutional]   
4  r3d100000006          Archaeology Data Service   [disciplinary]   

                                             subject  \
0  [1 Humanities and Social Sciences, 111 Social ...   
1  [1 Humanities and Social Sciences, 102 History...   
2  [1 Humanities and Social Sciences, 104 Linguis...   
3  [1 Humanities and Social Sciences, 111 Social ...   
4  [1 Humanities and Social Sciences, 101 Ancient...   

                     provider_type  \
0                   [dataProvider]   
1                   [dataProvider]   
2  [dataProvider, serviceProvider]   
3  [dataProvider, serviceProvider]   
4  [dataProvider, serviceProvider]   

                                             keyword  \
0  [FAIR, Middle East, crime, demography, economy...   
1                                       [US History]   
2  [Australian German, FOLK, German dialects, Pfe...   
3  [FAIR, census, demographic survey, demography,...   
4  [FAIR, archaeology, cultural heritage, prehist...   

                                         institution  
0  [[Odum Institute for Research in Social Scienc...  
1  [[The U.S. National Archives and Records Admin...  
2  [[Institut für Deutsche Sprache, Archiv für Ge...  
3  [[Odum Institute for Research in Social Scienc...  
4  [[Arts and Humanities Research Council, [AHRC]...

**HERE I AM FILTERING SERVICE PROVIDERS OUT!!**

In [4]:
re3data_df = re3data_df.explode('provider_type')
re3data_df = re3data_df[re3data_df.provider_type != 'serviceProvider']

In [5]:
re3data_df.describe(include='all')

re3data_id repository_name            type  \
count           2467            2467            2467   
unique          2466            2463               9   
top     r3d100011987         Landmap  [disciplinary]   
freq               2               2            1573   

                                                  subject provider_type  \
count                                                2467          2459   
unique                                               1282             1   
top     [1 Humanities and Social Sciences, 2 Life Scie...  dataProvider   
freq                                                  200          2459   

                    keyword                                        institution  
count                  2467                                               2467  
unique                 2248                                               2447  
top     [multidisciplinary]  [[National Center for Biotechnology Informatio...  
freq                    181                                                  6

**openDOAR**

In [6]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'opendoar_id': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    },
                        usecols=['opendoar_id', 'repository_name', 'subject', 'type', 'institution'])
opendoar_df.head()

opendoar_id                                    repository_name  \
0          101                      utrecht university repository   
1          115  dspace at indian institute of management kozhi...   
2           41             caltech engineering and science online   
3          119                 dcu online research access service   
4          129                            earth-prints repository   

            type                                            subject  \
0  institutional                                [multidisciplinary]   
1  institutional  [ecology and environment, social sciences gene...   
2  institutional  [biology and biochemistry, chemistry and chemi...   
3  institutional                                [multidisciplinary]   
4   disciplinary                     [earth and planetary sciences]   

                                         institution  
0  [[university of utrecht, [universiteit utrecht...  
1  [[indian institute of management kozhikode, [i...  
2  [[california institute of technology, [caltech...  
3  [[dublin city university, [dcu], ie, [], , htt...  
4  [[istituto nazionale di geofisica e vulcanolog...

In [7]:
opendoar_df.describe(include='all')

opendoar_id repository_name           type              subject  \
count    5707.000000            5707           5707                 5707   
unique           NaN            5670              4                  820   
top              NaN            arch  institutional  [multidisciplinary]   
freq             NaN               3           5067                 3212   
mean     4008.118801             NaN            NaN                  NaN   
std      2869.948770             NaN            NaN                  NaN   
min         2.000000             NaN            NaN                  NaN   
25%      1823.000000             NaN            NaN                  NaN   
50%      3361.000000             NaN            NaN                  NaN   
75%      5095.000000             NaN            NaN                  NaN   
max     10175.000000             NaN            NaN                  NaN   

                                              institution  
count                                                5707  
unique                                               5098  
top     [[rijksuniversiteit groningen, [rug], nl, [], ...  
freq                                                   26  
mean                                                  NaN  
std                                                   NaN  
min                                                   NaN  
25%                                                   NaN  
50%                                                   NaN  
75%                                                   NaN  
max                                                   NaN

**ROAR**

In [45]:
roar_df = pd.read_csv('../data/raw/export_roar_CSV.csv',
                     usecols=['eprintid', 'home_page', 'title', 'location_country', 'subjects'])
roar_df.head()

eprintid                                          home_page  \
0       921             http://alcme.oclc.org/ndltd/index.html   
1      1489  http://prensahistorica.mcu.es/prensahistorica/...   
2       606                   http://hal.archives-ouvertes.fr/   
3       606                                                NaN   
4       606                                                NaN   

                                               title location_country subjects  
0  Networked Digital Library of Theses and Disser...               us      NaN  
1                Virtual Library of Historical Press               es      NaN  
2                        HAL: Hyper Article en Ligne               fr      NaN  
3                                                NaN              NaN      NaN  
4                                                NaN              NaN      NaN

In [43]:
# roar_df.drop_duplicates(subset=['home_page', 'title' , 'location_country', 'subjects'], keep=False, inplace=True)

In [47]:
roar_df[roar_df.eprintid == 2303]

eprintid home_page                                          title  \
106      2303       NaN  Faculty Scholarship at The Claremont Colleges   
107      2303       NaN                                            NaN   
108      2303       NaN                                            NaN   
109      2303       NaN                                            NaN   
110      2303       NaN                                            NaN   
111      2303       NaN                                            NaN   
112      2303       NaN                                            NaN   
113      2303       NaN                                            NaN   
114      2303       NaN                                            NaN   
115      2303       NaN                                            NaN   
116      2303       NaN                                            NaN   
117      2303       NaN                                            NaN   

    location_country subjects  
106               us       AS  
107              NaN       BF  
108              NaN       BL  
109              NaN       CC  
110              NaN       GN  
111              NaN       H1  
112              NaN       HB  
113              NaN       JA  
114              NaN       LB  
115              NaN       NX  
116              NaN       PQ  
117              NaN       QA

In [44]:
roar_df.describe(include='all')

eprintid                  home_page                      title  \
count    5314.000000                       5263                       5268   
unique           NaN                       5156                       5027   
top              NaN  http://ir.lib.isu.edu.tw/  Repositorio Institucional   
freq             NaN                          3                          7   
mean     6389.464434                        NaN                        NaN   
std      5159.573937                        NaN                        NaN   
min         1.000000                        NaN                        NaN   
25%      1490.250000                        NaN                        NaN   
50%      4990.500000                        NaN                        NaN   
75%     10452.750000                        NaN                        NaN   
max     17302.000000                        NaN                        NaN   

       location_country subjects  
count              5024     1225  
unique              134      123  
top                  us       H1  
freq                877      147  
mean                NaN      NaN  
std                 NaN      NaN  
min                 NaN      NaN  
25%                 NaN      NaN  
50%                 NaN      NaN  
75%                 NaN      NaN  
max                 NaN      NaN

**FAIRsharing**

In [11]:
fairsharing_df = pd.read_csv('../data/raw/FAIRsharingDBrec_summary20210304.csv', 
                             delimiter='|', header=0,
                             names=['full_name', 'short_name', 'fs_url', 'url', 'countries', 'subjects'])
fairsharing_df.head()

full_name  short_name  \
0                                            GenBank     GenBank   
1                                          GlycoNAVI   GlycoNAVI   
2                                           ADHDgene    ADHDgene   
3  Allele frequency resource for research and tea...      ALFRED   
4               Animal Transcription Factor Database  AnimalTFDB   

                                              fs_url  \
0  https://fairsharing.org/10.25504/FAIRsharing.9...   
1  https://fairsharing.org/10.25504/FAIRsharing.w...   
2  https://fairsharing.org/10.25504/FAIRsharing.m...   
3  https://fairsharing.org/10.25504/FAIRsharing.y...   
4  https://fairsharing.org/10.25504/FAIRsharing.e...   

                                           url  \
0        https://www.ncbi.nlm.nih.gov/genbank/   
1                       https://glyconavi.org/   
2                     http://adhd.psych.ac.cn/   
3                   http://alfred.med.yale.edu   
4  http://bioinfo.life.hust.edu.cn/AnimalTFDB/   

                            countries  \
0  European Union,Japan,United States   
1                               Japan   
2                               China   
3                       United States   
4                               China   

                                            subjects  
0  Bioinformatics,Data Management,Data Submission...  
1  Chemistry,Glycomics,Life Science,Organic Chemi...  
2                        Biomedical Science,Genetics  
3                                       Life Science  
4                                       Life Science

In [12]:
fairsharing_df.describe(include='all')

full_name short_name  \
count       1752       1752   
unique      1752       1741   
top       CiteAb        CGD   
freq           1          3   

                                                   fs_url  \
count                                                1752   
unique                                               1752   
top     https://fairsharing.org/10.25504/FAIRsharing.1...   
freq                                                    1   

                           url      countries      subjects  
count                     1752           1749          1690  
unique                    1752            178           834  
top     http://www.plexdb.org/  United States  Life Science  
freq                         1            588           367